In [36]:
import pandas as pd
import os, re, sys, shutil, subprocess
from copy import deepcopy
import seaborn
from Bio import AlignIO, SeqIO, Align, Phylo
import ete3

ncbi = ete3.NCBITaxa()

# ete3 example of how to pass TaxID and get name
# ncbi.translate_to_names([1166948])
# ['Halomonas xinjiangensis']

In [37]:
os.chdir('/nobackup1c/users/payette/eggNOGbyClass1/bipartitions')
#%cd bipartitions

In [38]:
!pwd

/nobackup1c/users/payette/eggNOGbyClass1/bipartitions


In [40]:
!ls -ltrh

total 992K
-rw-rw-r-- 1 payette payette 373K Jan 13  2021 COG1346-cluster0.splits.nex
-rw-rw-r-- 1 payette payette 612K Feb 25  2021 COG3847-cluster0.splits.nex
drwxrwxr-x 2 payette payette 4.0K Oct  8 16:45 archive


In [6]:
def nexus_taxa_rewrite(nex_file_path):
    outputname2 = str(nex_file_path)+'.nex2'
    outF = open(outputname2, "w")      
    with open(nex_file_path) as fp:
        line = fp.readline()
        cnt = 1
        while line:
            if line.startswith('[')==True:
                num_index = re.findall(r"\[\s*\+?(-?\d+)\s*\]", line)
                taxid_index = (re.findall(r"\'*\+?(-?\d+)\.", line))
                name_str=ncbi.translate_to_names([int(taxid_index[0])])
                clean_name_str=str(name_str[0].replace(' ','_'))
                clean_name_str=str(clean_name_str.replace('(','_'))
                clean_name_str=str(clean_name_str.replace(')','_'))
                clean_name_str=str(clean_name_str.replace(':','_'))
                clean_name_str=str(clean_name_str.replace('=','_'))
                #print(clean_name_str)
                if len(clean_name_str) > 0:
                    line = re.sub(str(taxid_index[0]),clean_name_str,line)
                #col_table[num_index[0]]=clean_name_str
                cnt += 1
            outF.write(line)
            #outF.write("\n")
            line = fp.readline()
    outF.close()

In [7]:
#def key2val(key,val):
#    df.iloc[int(key-1),(val-1)]=True

In [8]:
def make_bipartition_table(nex_file_path):
    def key2val(key,val):
        df.iloc[int(key-1),(val-1)]=True
    
    ncbi = ete3.NCBITaxa()
    #Populate col table, then support table, make df, populate df, print
    col_table = {}
    support_table = {}
    outputname = str(nex_file_path)+'.csv'
    
    with open(nex_file_path) as fp:
        try:
            line = fp.readline()
            cnt = 1
            while line:
                if line.startswith('[')==True:
                    num_index = re.findall(r"\[\s*\+?(-?\d+)\s*\]", line)
                    taxid_index = (re.findall(r"\'*\+?(-?\d+)\.", line))
                    name_str=ncbi.translate_to_names([int(taxid_index[0])])
                    clean_name_str=str(name_str[0].replace(' ','_'))
                    col_table[num_index[0]]=clean_name_str
                    cnt += 1
                if line.startswith('/n')==True:
                    line=fp.readline()
                else:
                    line=fp.readline()
        except:
            print("File not found.")
            return

    with open(nex_file_path) as fp2:
        line = fp2.readline()
        cnt = 1
        while line:
            if line.startswith('	')==True:
                line_split = line.split()
                support_table[cnt]=line_split[0]
                cnt += 1
                line=fp2.readline()
            else:
                line=fp2.readline()

    print(len(col_table),len(support_table))
    df =pd.DataFrame(index=support_table.values(),columns=col_table.items())
    col_bool = {}
    with open(nex_file_path) as fp:
        line = fp.readline()
        cnt = 1
        while line:
            if line.startswith('	')==True:
                #print(line)
                line_split = line.split()
                #print(line_split[1:len(col_table)])
                col_bool[cnt]=line_split[1:len(col_table)]
                cnt += 1
                line=fp.readline()
            else:
                line=fp.readline()
                #print(line)
    
    for each,key in zip(col_bool.values(),col_bool.keys()):
    #val=str(each).replace(',','')
    #print(type(each))
    #print(val)
    #print(type(val))
    #val.replace('[','')
        print('row:',key)
        for col_num in each:
            val=int(col_num.replace(',',''))
            print(val)
            key2val(key,val)
    #print(type(key))
    #df.iloc[key,(val.replace(' ','')-1)]=True
    
    df.to_csv(outputname)
    return(df)

In [9]:
#Example make_bipartition_table

In [41]:
make_bipartition_table('COG3847-cluster0.splits.nex')

589 4913
row: 1
2
row: 2
4
row: 3
5
row: 4
4
5
row: 5
10
row: 6
218
row: 7
10
218
row: 8
11
row: 9
10
11
218
row: 10
168
row: 11
503
row: 12
504
row: 13
503
504
row: 14
505
row: 15
503
504
505
row: 16
506
row: 17
507
row: 18
508
row: 19
507
508
row: 20
509
row: 21
507
508
509
row: 22
506
507
508
509
row: 23
503
504
505
506
507
508
509
row: 24
510
row: 25
503
504
505
506
507
508
509
510
row: 26
168
503
504
505
506
507
508
509
510
row: 27
10
11
168
218
503
504
505
506
507
508
509
510
row: 28
4
5
10
11
168
218
503
504
505
506
507
508
509
510
row: 29
6
row: 30
7
row: 31
6
7
row: 32
4
5
6
7
10
11
168
218
503
504
505
506
507
508
509
510
row: 33
15
row: 34
16
row: 35
17
row: 36
18
row: 37
17
18
row: 38
22
row: 39
17
18
22
row: 40
16
17
18
22
row: 41
19
row: 42
16
17
18
19
22
row: 43
15
16
17
18
19
22
row: 44
20
row: 45
95
row: 46
264
row: 47
95
264
row: 48
20
95
264
row: 49
89
row: 50
90
row: 51
89
90
row: 52
93
row: 53
89
90
93
row: 54
91
row: 55
92
row: 56
91
92
row: 57
89
90
91
92
93
row: 

304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
324
325
326
368
369
370
371
372
373
374
375
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
row: 342
288
row: 343
274
275
276
277
278
279
280
287
288
289
291
292
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
324
325
326
368
369
370
371
372
373
374
375
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
row: 344
323
row: 345
274
275
276
277
278
279
280
287
288
289
291
292
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
368
369
370
371
372
373
374
375
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
row: 346
290
row: 347
293
row: 348
294
row: 349
293
294
row: 350
295
row: 351
29

339
340
341
342
343
344
345
346
347
348
349
350
351
352
363
364
365
367
368
369
370
371
372
373
374
375
376
381
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
419
502
503
504
505
506
507
508
509
510
516
517
518
519
520
521
522
523
524
525
526
527
528
529
530
531
532
533
534
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
568
575
576
577
578
row: 503
37
row: 504
38
row: 505
39
row: 506
38
39
row: 507
37
38
39
row: 508
40
row: 509
43
row: 510
44
row: 511
43
44
row: 512
45
row: 513
43
44
45
row: 514
46
row: 515
43
44
45
46
row: 516
40
43
44
45
46
row: 517
51
row: 518
52
row: 519
55
row: 520
52
55
row: 521
51
52
55
row: 522
53
row: 523
54
row: 524
53
54
row: 525
51
52
53
54
55
row: 526
40
43
44
45
46
51
52
53
54
55
row: 527
41
row: 528
42
row: 529
41
42
row: 530
272
row: 531
41
42
272
row: 532
47
row: 533
48
row: 534
47
48
row: 535
41
42
47
48
272
row: 536
49
row: 537
50
row: 538
49
50
row: 539

126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
144
145
146
147
148
149
150
151
152
153
156
157
158
159
160
161
162
163
167
201
204
234
235
236
237
238
239
269
270
273
327
328
355
366
377
378
379
380
382
383
387
405
406
407
408
409
410
411
412
413
414
415
416
417
418
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
501
565
569
570
571
572
573
574
582
583
584
585
586
587
588
589
row: 761
23
row: 762
24
row: 763
23
24
row: 764
25
row: 765
26
row: 766
273
row: 767
26
273
row: 768
144
row: 769
422
row: 770
423
row: 771
424
row: 772
423
424
row: 773
425
row: 774
423
424
425
row: 775
426
row: 776
427
row: 777
426
427
row: 778
423
424
425
426
427
row: 779
428
row: 780
429
row: 781
428
429
row: 782
423
424
425
426
427
428
429
row: 783
422
423
424
425
426


412
413
414
415
416
417
418
row: 1010
501
row: 1011
405
406
407
408
409
410
411
412
413
414
415
416
417
418
501
row: 1012
32
405
406
407
408
409
410
411
412
413
414
415
416
417
418
501
row: 1013
380
row: 1014
32
380
405
406
407
408
409
410
411
412
413
414
415
416
417
418
501
row: 1015
134
row: 1016
32
134
380
405
406
407
408
409
410
411
412
413
414
415
416
417
418
501
row: 1017
33
row: 1018
34
row: 1019
33
34
row: 1020
145
row: 1021
146
row: 1022
145
146
row: 1023
33
34
145
146
row: 1024
35
row: 1025
33
34
35
145
146
row: 1026
36
row: 1027
33
34
35
36
145
146
row: 1028
201
row: 1029
377
row: 1030
378
row: 1031
377
378
row: 1032
379
row: 1033
377
378
379
row: 1034
201
377
378
379
row: 1035
33
34
35
36
145
146
201
377
378
379
row: 1036
123
row: 1037
124
row: 1038
123
124
row: 1039
125
row: 1040
126
row: 1041
125
126
row: 1042
129
row: 1043
130
row: 1044
129
130
row: 1045
125
126
129
130
row: 1046
127
row: 1047
128
row: 1048
127
128
row: 1049
125
126
127
128
129
130
row: 1050
131
row: 105

...

322
323
324
325
326
368
369
370
371
372
373
374
375
376
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
row: 4710
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
96
141
142
164
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
265
266
267
268
271
272
353
354
356
357
358
359
360
361
362
384
385
511
566
row: 4711
1
2
3
31
97
98
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
136
137
138
139
140
143
147
148
149
150
151
152
153
157
158
159
160
161
162
167
169
170
204
234
235
236
237
238
239
258
259
260
261
262
263
327
328
355
366
387
442
574
row: 4712
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
136
137
138
139
140
147
148
149
150
167
204
234
235
236
237
238
239
442
row: 4713
1
2
3
23
24
25
26
27
28
29
30
3

271
272
354
356
357
358
359
360
361
362
384
385
386
490
491
492
493
494
495
496
497
498
499
500
512
513
514
515
566
579
580
581
row: 4765
205
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
525
568
row: 4766
154
155
165
166
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
202
203
205
206
207
208
209
210
211
212
213
214
215
216
217
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
363
364
365
367
381
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
419
502
525
568
row: 4767
516
517
518
519
520
521
522
523
524
575
576
577
578
row: 4768
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325


43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
265
266
267
268
271
272
353
356
357
358
359
360
361
362
384
385
566
row: 4820
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
265
266
267
268
271
272
353
356
357
358
359
360
361
362
384
385
512
513
514
515
566
row: 4821
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
96
97
98
143
169
170
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
265
266
267
268
27

202
203
205
206
207
208
209
210
211
212
213
214
215
216
217
218
264
281
282
283
284
285
286
327
328
363
364
365
366
367
381
419
502
503
504
505
506
507
508
509
510
526
row: 4875
63
64
65
66
67
68
69
70
71
97
98
108
109
110
169
170
269
270
row: 4876
27
28
29
30
63
64
65
66
67
68
69
70
71
97
98
108
109
110
169
170
269
270
420
row: 4877
37
38
39
61
62
74
75
row: 4878
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
58
61
62
72
73
74
75
78
79
80
81
82
83
84
85
86
87
88
231
272
row: 4879
59
60
76
77
96
row: 4880
56
57
59
60
76
77
96
row: 4881
27
28
29
30
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
96
97
98
108
109
110
141
142
169
170
231
269
270
272
356
357
358
359
360
361
362
420
row: 4882
258
259
260
261
262
263
266
267
268
354
512
513
514
515
row: 4883
219
220
221
222
223
224
225
226
227
228
229
230
232
233
258
259
260
261
262
263
265
266
267
268
271
354
384
385
512
513

1                         2  \
    Variovorax_paradoxus_EPS Variovorax_paradoxus_110B   
100                      NaN                      True   
100                      NaN                       NaN   
100                      NaN                       NaN   
94                       NaN                       NaN   
100                      NaN                       NaN   
..                       ...                       ...   
0                        NaN                       NaN   
0                        NaN                       NaN   
0                       True                      True   
0                        NaN                       NaN   
0                       True                      True   

                            3                               4  \
    Variovorax_paradoxus_S110 Desulfovibrio_fructosivorans_JJ   
100                       NaN                             NaN   
100                       NaN                            True   
100                       NaN                             NaN   
94                        NaN                            True   
100                       NaN                             NaN   
..                        ...                             ...   
0                         NaN                             NaN   
0                         NaN                             NaN   
0                        True                             NaN   
0                         NaN                             NaN   
0                        True                             NaN   

                                  5                                     6  \
    Desulfovibrio_fructosivorans_JJ Desulfovibrio_alcoholivorans_DSM_5433   
100                             NaN                                   NaN   
100                             NaN                                   NaN   
100                            True                                   NaN   
94                             True                                   NaN   
100                             NaN                                   NaN   
..                              ...                                   ...   
0                               NaN                                   NaN   
0                               NaN                                   NaN   
0                               NaN                                   NaN   
0                               NaN                                   NaN   
0                               NaN                                   NaN   

                                        7                             8  \
    Desulfovibrio_alcoholivorans_DSM_5433 Desulfovibrio_magneticus_RS-1   
100                                   NaN                           NaN   
100                                   NaN                           NaN   
100                                   NaN                           NaN   
94                                    NaN                           NaN   
100                                   NaN                           NaN   
..                                    ...                           ...   
0                                     NaN                           NaN   
0                                     NaN                           NaN   
0                                     NaN                           NaN   
0                                     NaN                           NaN   
0                                     NaN                           NaN   

                                9                    10  ...  \
    Desulfovibrio_magneticus_RS-1 Desulfovibrio_sp._U5L  ...   
100                           NaN                   NaN  ...   
100                           NaN                   NaN  ...   
100                           NaN                   NaN  ...   
94                            NaN                   NaN  ...   
100                           NaN                  True  ...   


In [18]:
#store the returned results as a specific dataframe (pandas)
table1 = make_bipartition_table('COG3847-cluster0.splits.nex')
#prints the key for each row, then values which are the column number (index for columns)

589 4913
row: 1
2
row: 2
4
row: 3
5
row: 4
4
5
row: 5
10
row: 6
218
row: 7
10
218
row: 8
11
row: 9
10
11
218
row: 10
168
row: 11
503
row: 12
504
row: 13
503
504
row: 14
505
row: 15
503
504
505
row: 16
506
row: 17
507
row: 18
508
row: 19
507
508
row: 20
509
row: 21
507
508
509
row: 22
506
507
508
509
row: 23
503
504
505
506
507
508
509
row: 24
510
row: 25
503
504
505
506
507
508
509
510
row: 26
168
503
504
505
506
507
508
509
510
row: 27
10
11
168
218
503
504
505
506
507
508
509
510
row: 28
4
5
10
11
168
218
503
504
505
506
507
508
509
510
row: 29
6
row: 30
7
row: 31
6
7
row: 32
4
5
6
7
10
11
168
218
503
504
505
506
507
508
509
510
row: 33
15
row: 34
16
row: 35
17
row: 36
18
row: 37
17
18
row: 38
22
row: 39
17
18
22
row: 40
16
17
18
22
row: 41
19
row: 42
16
17
18
19
22
row: 43
15
16
17
18
19
22
row: 44
20
row: 45
95
row: 46
264
row: 47
95
264
row: 48
20
95
264
row: 49
89
row: 50
90
row: 51
89
90
row: 52
93
row: 53
89
90
93
row: 54
91
row: 55
92
row: 56
91
92
row: 57
89
90
91
92
93
row: 

398
400
401
row: 432
399
row: 433
393
394
396
397
398
399
400
401
row: 434
395
row: 435
393
394
395
396
397
398
399
400
401
row: 436
388
393
394
395
396
397
398
399
400
401
row: 437
391
row: 438
392
row: 439
391
392
row: 440
388
391
392
393
394
395
396
397
398
399
400
401
row: 441
389
row: 442
388
389
391
392
393
394
395
396
397
398
399
400
401
row: 443
390
row: 444
388
389
390
391
392
393
394
395
396
397
398
399
400
401
row: 445
402
row: 446
403
row: 447
402
403
row: 448
404
row: 449
402
403
404
row: 450
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
row: 451
525
row: 452
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
525
row: 453
568
row: 454
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
525
568
row: 455
516
row: 456
518
row: 457
521
row: 458
518
521
row: 459
519
row: 460
518
519
521
row: 461
516
518
519
521
row: 462
517
row: 463
520
row: 464
517
520
row: 465
516
517
518
519
520
521
row: 466
388
389
390
391
392
393
394
3

136
137
138
139
140
144
145
146
147
148
149
150
151
152
153
156
157
158
159
160
161
162
163
167
201
204
234
235
236
237
238
239
269
270
273
327
328
355
366
377
378
379
380
382
383
387
405
406
407
408
409
410
411
412
413
414
415
416
417
418
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
501
511
565
569
570
571
572
573
574
582
583
584
585
586
587
588
589
row: 759
511
row: 760
1
2
3
23
24
25
26
27
28
29
30
31
32
33
34
35
36
63
64
65
66
67
68
69
70
71
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
144
145
146
147
148
149
150
151
152
153
156
157
158
159
160
161
162
163
167
201
204
234
235
236
237
238
239
269
270
273
327
328
355
366
377
378
379


row: 1103
117
row: 1104
113
117
row: 1105
111
112
113
114
115
116
117
118
234
235
236
237
238
239
row: 1106
121
row: 1107
122
row: 1108
121
122
row: 1109
111
112
113
114
115
116
117
118
121
122
234
235
236
237
238
239
row: 1110
102
111
112
113
114
115
116
117
118
119
121
122
234
235
236
237
238
239
row: 1111
103
row: 1112
104
row: 1113
105
row: 1114
104
105
row: 1115
103
104
105
row: 1116
102
103
104
105
111
112
113
114
115
116
117
118
119
121
122
234
235
236
237
238
239
row: 1117
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
234
235
236
237
238
239
row: 1118
136
row: 1119
139
row: 1120
136
139
row: 1121
137
row: 1122
138
row: 1123
137
138
row: 1124
136
137
138
139
row: 1125
140
row: 1126
136
137
138
139
140
row: 1127
204
row: 1128
136
137
138
139
140
204
row: 1129
167
row: 1130
136
137
138
139
140
167
204
row: 1131
147
row: 1132
148
row: 1133
147
148
row: 1134
149
row: 1135
147
148
149
row: 1136
150
row: 1137
147
148
149
150
row: 1138
136
137
138
139
1

314
315
316
317
318
319
320
321
322
323
324
325
326
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
row: 1328
274
275
276
277
278
279
280
287
288
289
291
292
297
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
368
369
370
371
372
373
374
375
376
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
row: 1329
388
391
392
row: 1330
390
402
403
404
row: 1331
389
390
402
403
404
row: 1332
388
389
390
391
392
402
403
404
row: 1333
281
282
283
284
285
286
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
row: 1334
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
368
369
370
371
372
373
374
375
376
388
389
390
391
39

...

329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
363
364
365
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
501
502
503
504
505
506
507
508
509
510
511
516
517
518
519
520
521
522
523
524
525
526
527
528
529
530
531
532
533
534
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
568
573
575
576
577
578
row: 4667
1
2
3
31
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
136
137
138
139
140
147
148
149
150
151
152
153
157
158
159
160
161
162
167
204
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
265
266
267
268
271
272
327
328
355
3

428
429
430
431
432
433
434
435
436
437
438
439
440
441
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
569
570
571
572
573
row: 4726
27
28
29
30
32
63
64
65
66
67
68
69
70
71
108
109
110
269
270
380
405
406
407
408
409
410
411
412
413
414
415
416
417
418
420
501
565
582
583
584
585
586
587
588
589
row: 4727
443
444
445
446
447
448
449
450
451
452
453
454
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
569
570
571
572
row: 4728
1
2
3
31
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
136
137
138
139
140
147
148
149
150
151
152
153
157
158
159
160
161
162
167
204
234
235
236
237
238
239
327
328
355
366
386
387
574
row: 4729
545
546
547
548
550
551
552
553
557
562
563
row: 4730
535
567
row: 4731
96
97
98
143
169
170
row: 4732
37
38
3

252
253
254
255
256
257
269
270
273
327
328
353
355
366
377
378
379
380
382
383
387
405
406
407
408
409
410
411
412
413
414
415
416
417
418
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
501
565
569
570
571
572
573
574
582
583
584
585
586
587
588
589
row: 4771
1
2
3
31
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
136
137
138
139
140
147
148
149
150
151
152
153
157
158
159
160
161
162
167
204
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
327
328
353
355
366
387
574
row: 4772
407
408
409
410
411
412
413
416
row: 4773
407
408
409
410
411
412
413
415
416
row: 4774
1
2
3
31
32
33
34
35
36
99
100
101
102
103
104
105
106
107
111
112
113
114
115
116
117
118
119
121
122
123
124
125
1

280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
368
369
370
371
372
373
374
375
376
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
516
517
518
519
520
521
525
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
568
row: 4828
205
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
368
369
370
371
372
373
374
375
376
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
516
517
518
519
520
521
525
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
567
568
row: 4829
329
330
331
332
333
334
335
336
337
338
339
340
341
342


83
84
85
86
87
88
96
97
98
108
109
110
141
142
169
170
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
258
259
260
261
262
263
265
266
267
268
269
270
271
272
354
356
357
358
359
360
361
362
384
385
420
512
513
514
515
566
row: 4885
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
27
28
29
30
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
108
109
110
141
142
151
152
153
154
155
159
160
161
165
166
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
202
203
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
281
282
283
284
285
286
327
328
354
356
357
358
359
360
361
362
363
364
365
366
367
381
384
385
419
420
502
503
504
505
506
507
50

In [42]:
table1.index #this is the bootstrap support for a given row/column of taxa as True/False

Index(['100', '100', '100', '94', '100', '100', '22', '100', '46', '100',
       ...
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '0'],
      dtype='object', length=4913)

In [21]:
table1.head()

1                         2  \
    Variovorax_paradoxus_EPS Variovorax_paradoxus_110B   
100                      NaN                      True   
100                      NaN                       NaN   
100                      NaN                       NaN   
94                       NaN                       NaN   
100                      NaN                       NaN   

                            3                               4  \
    Variovorax_paradoxus_S110 Desulfovibrio_fructosivorans_JJ   
100                       NaN                             NaN   
100                       NaN                            True   
100                       NaN                             NaN   
94                        NaN                            True   
100                       NaN                             NaN   

                                  5                                     6  \
    Desulfovibrio_fructosivorans_JJ Desulfovibrio_alcoholivorans_DSM_5433   
100                             NaN                                   NaN   
100                             NaN                                   NaN   
100                            True                                   NaN   
94                             True                                   NaN   
100                             NaN                                   NaN   

                                        7                             8  \
    Desulfovibrio_alcoholivorans_DSM_5433 Desulfovibrio_magneticus_RS-1   
100                                   NaN                           NaN   
100                                   NaN                           NaN   
100                                   NaN                           NaN   
94                                    NaN                           NaN   
100                                   NaN                           NaN   

                                9                    10  ...  \
    Desulfovibrio_magneticus_RS-1 Desulfovibrio_sp._U5L  ...   
100                           NaN                   NaN  ...   
100                           NaN                   NaN  ...   
100                           NaN                   NaN  ...   
94                            NaN                   NaN  ...   
100                           NaN                  True  ...   

                              580                           581  \
    Marinobacter_lipolyticus_SM19 Nitrosococcus_halophilus_Nc_4   
100                           NaN                           NaN   
100                           NaN                           NaN   
100                           NaN                           NaN   
94                            NaN                           NaN   
100                           NaN                           NaN   

                           582                        583  \
    Pirellula_staleyi_DSM_6068 Pirellula_staleyi_DSM_6068   
100                        NaN                        NaN   
100                        NaN                        NaN   
100                        NaN                        NaN   
94                         NaN                        NaN   
100                        NaN                        NaN   

                           584                        585  \
    Pirellula_staleyi_DSM_6068 Pirellula_staleyi_DSM_6068   
100                        NaN                        NaN   
100                        NaN                        NaN   
100                        NaN                        NaN   
94                         NaN                        NaN   
100                        NaN                        NaN   

                           586                        587  \
    Pirellula_staleyi_DSM_6068 Pirellula_staleyi_DSM_6068   
100                        NaN                        NaN   
100                        NaN                        NaN   
100                        NaN                        NaN   
94                

In [22]:
!ls -ltrh

total 4.4M
-rw-rw-r-- 1 payette payette 373K Jan 13  2021 COG1346-cluster0.splits.nex
-rw-rw-r-- 1 payette payette 612K Feb 25  2021 COG3847-cluster0.splits.nex
drwxrwxr-x 2 payette payette 4.0K Oct  8 13:45 archive
-rw-rw-r-- 1 payette payette 3.4M Oct  8 14:16 COG3847-cluster0.splits.nex.csv


In [25]:
for line in open('COG3847-cluster0.splits.nex.csv').readlines():
    print(line)

,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,173,174,175,176,177,178,179,180,181,182,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,238,239,240,241,242,243,244,245,246,247,248,249,250,251,252,253,254,255,256,257,258,259,260,261,262,263,264,265,266,267,268,269,270,271,272,273,274,275,276,277

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
####

In [26]:
for line in open('COG1346-cluster0.splits.nex').readlines():
    print(line)

#nexus



BEGIN Taxa;

DIMENSIONS ntax=625;

TAXLABELS

[1] '1166948.JPZL01000005_gene3351'

[2] '1121939.L861_06940'

[3] '42565.FP66_08790'

[4] '1397528.Q671_03930'

[5] '1178482.BJB45_14670'

[6] '1396858.Q666_11925'

[7] '351348.Maqu_0448'

[8] '1122197.ATWI01000010_gene1119'

[9] '225937.HP15_199'

[10] '443152.MDG893_14950'

[11] '1415754.JQMK01000002_gene2359'

[12] '1288826.MSNKSG1_16871'

[13] '1479237.JMLY01000001_gene998'

[14] '1318628.MARLIPOL_07244'

[15] '1118153.MOY_03558'

[16] '999141.GME_18992'

[17] '232346.JHQL01000006_gene2932'

[18] '1479235.KK366039_gene2348'

[19] '1380358.JADJ01000037_gene2675'

[20] '1415755.JQLV01000001_gene858'

[21] '1504981.KO116_4627'

[22] '574966.KB898658_gene2760'

[23] '1238190.AMQY01000025_gene108'

[24] '1121943.KB899998_gene1640'

[25] '290398.Csal_0373'

[26] '1492922.GY26_07265'

[27] '1046724.KB889828_gene2957'

[28] '270374.MELB17_21081'

[29] '1168065.DOK_18600'

[30] '1123279.ATUS01000001_gene2180'

[31] '1121374.KB891591_g


	0	 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 278 279 280 281 282 283 284 285 286 292 293 294 295 296 297 303 304 305 307 308 310 311 342 343 344 345 346 347 348 496 497 498 499 509 510 511 512 521 524 556,

	0	 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 306 312 313 314 315 316 317 318 319 320 321 322 323 324 325 326 327 328 329 330 331 332 333 334 335 336 337 338 339 359 360 361 369 370 371 372 373 374 375 376 377 378 383 384 385 386 387 388 389 390 391 392 393 394 395 396 397 398 399 400 401 402 403 404 405 406 407 408 409 410 411 412 413 414 415 416 417 418

In [ ]:
nexus_taxa_rewrite('COG1346-cluster0.splits.nex')

In [29]:
!ls -ltrh

total 4.4M
-rw-rw-r-- 1 payette payette 373K Jan 13  2021 COG1346-cluster0.splits.nex
-rw-rw-r-- 1 payette payette 612K Feb 25  2021 COG3847-cluster0.splits.nex
drwxrwxr-x 2 payette payette 4.0K Oct  8 13:45 archive
-rw-rw-r-- 1 payette payette 3.4M Oct  8 14:16 COG3847-cluster0.splits.nex.csv
-rw-rw-r-- 1 payette payette 386K Oct  8 14:18 COG1346-cluster0.splits.nex.nex2


In [30]:
for line in open('COG1346-cluster0.splits.nex.nex2').readlines():
    print(line)

#nexus



BEGIN Taxa;

DIMENSIONS ntax=625;

TAXLABELS

[1] 'Halomonas_xinjiangensis.JPZL01000005_gene3351'

[2] 'Halomonas_anticariensis_FP35___DSM_16096.L861_06940'

[3] 'Halomonas_salina.FP66_08790'

[4] 'Halomonas_sp._PBN3.Q671_03930'

[5] 'Halomonas_huangheensis.BJB45_14670'

[6] 'Marinobacter_sp._ES-1.Q666_11925'

[7] 'Marinobacter_hydrocarbonoclasticus_VT8.Maqu_0448'

[8] 'Marinobacter_daepoensis_DSM_16072.ATWI01000010_gene1119'

[9] 'Marinobacter_adhaerens_HP15.HP15_199'

[10] 'Marinobacter_algicola_DG893.MDG893_14950'

[11] 'Marinobacter_sp._MCTG268.JQMK01000002_gene2359'

[12] 'Marinobacter_santoriniensis_NKSG1.MSNKSG1_16871'

[13] 'Marinobacter_sp._HL-58.JMLY01000001_gene998'

[14] 'Marinobacter_lipolyticus_SM19.MARLIPOL_07244'

[15] 'Halomonas_sp._GFAJ-1.MOY_03558'

[16] 'Halomonas_sp._TD01.GME_18992'

[17] 'Halomonas_alkaliantarctica.JHQL01000006_gene2932'

[18] 'Halomonas_sp._HL-48.KK366039_gene2348'

[19] 'Halomonas_sp._23_GOM-1509m.JADJ01000037_gene2675'

[20] 'Halomona

	0	 22 23,

	0	 369 370 371 372 373 375 376 377 378 526,

	0	 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 161 165 166 167 168 169 170 171 172 177 309 358 555,

	0	 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 165 166 167 168 169 170 171 172 174 177 309 358 555,

	0	 566 567 573 574 575,

	0	 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 12

In [32]:
##############
#    FIN
#############